The purpose of this notebook is to scrape a website of all the download links for data files. This is specifically to scrape all the demographic data files from the NYU Ferman Center website.

https://furmancenter.org/files/NDP/excel_downloads/BK01_NeighborhoodDataProfile.xlsx
https://furmancenter.org/files/NDP/excel_downloads/BX10_NeighborhoodDataProfile.xlsx
https://furmancenter.org/files/NDP/excel_downloads/QN04_NeighborhoodDataProfile.xlsx

1. Get a list of all the file names
2. Run through them and download the files
3. Turn the excel files into JSON files
4. Delete the original excel files if necessary

## 1. Creating Code Lists

In [124]:
import pandas as pd
import numpy as np
import requests
import itertools
import xlrd
import csv
import os
import json
import mysql.connector
import sqlalchemy
from credentials import MYSQL_PASSWORD
pd.set_option('display.max_rows', 5000)

In [2]:
# Function to create the necessary lists
def get_codes(string, n):
    
    ''' 
    Takes in a string and a number (n).
    Returns the concatenation of the string and the range of numbers from 1 up to n
    '''
    
    lst = []
    
    for x in range(1,n+1):

        if x < 10:
            code = string + '0' + str(x)
        else:
            code = string + str(x)

        lst.append(code)
    
    return lst


In [3]:
# Create the list of region codes

# Brooklyn
bk = get_codes('BK',18)

# Bronx
bx = get_codes('BX', 12)

# Manhattan
mn = get_codes('MN', 12)

# Queens
qn = get_codes('QN', 14)

# Staten Island
si = get_codes('SI', 3)

code_list = list(itertools.chain.from_iterable([bk, bx, mn, qn, si]))

## 2. Download the files

In [7]:
## Crawl the website and download all of the data files

data_dir = '/Users/mareksalamon/Desktop/Politiker/Code/App Demo/Politiker/public/data'

for code in code_list:
    
    file_url = f"https://furmancenter.org/files/NDP/excel_downloads/{code}_NeighborhoodDataProfile.xlsx"

    r = requests.get(file_url, stream = True) 

    with open(data_dir + f"/sba_demos_2/{code}.xlsx","wb") as excel: 
        for chunk in r.iter_content(chunk_size=1024): 

             # writing one chunk at a time to excel file 
            if chunk: 
                excel.write(chunk) 

In [14]:
# Reading the data in the excel files and concatenating the contents to a single dataframe

path = data_dir + "/sba_demos_2"
files = os.listdir(path)

files_xlsx = [f for f in files if f[-4:] == 'xlsx']

df = pd.DataFrame()

for f in files_xlsx:
    
    path = data_dir + f"/sba_demos_2/{f}"
    sheet = f[0:2] + ' ' + f[2:4] + ' ' + 'Data'
    data = pd.read_excel(path, f"{sheet}")
    df = df.append(data)

#     print(path)
#     print(sheet)
#     print("\n")

In [15]:
# Processing the dataframe
df = df.iloc[:, :-4]
df['Community District'] = df['Community District'].str.replace(" ","")
df.rename(columns=lambda x: str(x).strip(), inplace=True)
df = df.where(df.notnull(), None)

In [25]:
df.head()

Community District             Name Indicator Category  \
0               QN04  Elmhurst/Corona       Demographics   
1               QN04  Elmhurst/Corona       Demographics   
2               QN04  Elmhurst/Corona       Demographics   
3               QN04  Elmhurst/Corona       Demographics   
4               QN04  Elmhurst/Corona       Demographics   

                 Indicator                              Indicator Description  \
0   Born in New York State  The percentage of city residents who were born...   
1      Disabled population  The percentage of the adult population who hav...   
2  Foreign-born population  The share of the population that is born outsi...   
3               Population  All people, both children and adults, living i...   
4      Population aged 65+  The percentage of residents who are aged 65 ye...   

      2000     2006     2010     2017     2018 boro_cd  
0     None    30.0%    30.1%    30.9%    31.3%     404  
1     None     None     5.7%     7.3%     4.2%     404  
2    66.8%    66.3%    63.9%    63.9%    64.2%     404  
3  142,022  138,593  136,517  146,301  150,131     404  
4     8.6%     9.8%    11.0%    11.6%    11.3%     404

In [17]:
# Create the list of 'boro_codes'

# Brooklyn
bk_bc = get_codes('3', 18)

# Bronx
bx_bc = get_codes('2', 12)

# Manhattan
mn_bc = get_codes('1', 12)

# Queens
qn_bc = get_codes('4', 14)

# Staten Island
si_bc = get_codes('5', 3)

bc_list = list(itertools.chain.from_iterable([bk_bc, bx_bc, mn_bc, qn_bc, si_bc]))

In [18]:
# Combine the code_list and bc_list into a dictionary of key, value pairs
stats_map_dic = dict(zip(code_list, bc_list))

In [ ]:
# Adding a new column to the dataframe based on the dictionary above
df["boro_cd"] = df["Community District"].map(stats_map_dic)

### Adding higher education info

In [119]:
# Adding higher education statistics (change link so that it automatically downloads it from the website: https://app.coredata.nyc/?mlb=false&ntii=pop_edu_collp_pct&ntr=Sub-Borough%20Area&mz=10&vtl=https%3A%2F%2Fthefurmancenter.carto.com%2Fu%2Fnyufc%2Fapi%2Fv2%2Fviz%2F98d1f16e-95fd-4e52-a2b1-b7abaf634828%2Fviz.json&mln=true&mlp=false&mlat=40.73257&ptsb=&nty=2018&mb=roadmap&pf=%7B%22subsidies%22%3Atrue%7D&md=table&mlv=false&mlng=-74.015226&btl=Borough&atp=neighborhoods#)
higher_ed = pd.read_csv(data_dir + "/sba_demos_2/sba_higher_ed.csv")
higher_ed = higher_ed[["long_name","Sub-Borough Area","2000","2006","2010","2017","2018"]]
higher_ed["Indicator Category"] = "Demographics"
higher_ed["Indicator Description"] = "The percentage of the population aged 25 and older that has completed a Bachelor's degree or other higher level of education."
higher_ed.columns = ['Indicator', 'Name', '2000', '2006', '2010', '2017', '2018',
                     'Indicator Category', 'Indicator Description'] 

# Renaming some of the community district names; the higher education data have different CD names
higher_ed_rename = {
    'Bay Ridge': 'Bay Ridge/Dyker Heights',
    'Brownsville/Ocean Hill': 'Brownsville',
    'Brooklyn Heights/Fort Greene': 'Fort Greene/Brooklyn Heights',
    'Chelsea/Clinton/Midtown': 'Clinton/Chelsea',
    'Flatbush': 'Flatbush/Midwood',
    'Greenwich Village/Financial District': 'Greenwich Village/Soho',
    'Highbridge/South Concourse': 'Highbridge/Concourse',
    'Jamaica': 'Jamaica/Hollis',
    'Kingsbridge Heights/Mosholu': 'Kingsbridge Heights/Bedford',
    'Middle Village/Ridgewood': 'Ridgewood/Maspeth',
    'Morningside Heights/Hamilton Heights': 'Morningside Heights/Hamilton',
    'Morrisania/Belmont':  'Morrisania/Crotona',
    'Mott Haven/Hunts Point':  'Mott Haven/Melrose',
    'North Crown Heights/Prospect Heights':  'Crown Heights/Prospect Heights',
    'Ozone Park/Woodhaven':'Kew Gardens/Woodhaven',
    'Riverdale/Kingsbridge':  'Riverdale/Fieldston',
    'Rockaways':  'Rockaway/Broad Channel',
    'Sheepshead Bay/Gravesend':  'Sheepshead Bay',
    'Soundview/Parkchester':  'Parkchester/Soundview',
    'South Crown Heights':  'South Crown Heights/Lefferts Gardens',
    'Sunnyside/Woodside':  'Woodside/Sunnyside',
    'University Heights/Fordham': 'Fordham/University Heights',
    'Williamsburg/Greenpoint':  'Greenpoint/Williamsburg',
    'North Shore': 'St. George/Stapleton',
    'Pelham Parkway': 'Morris Park/Bronxdale',
    'South Shore': 'Tottenville/Great Kills',
    'Mid-Island': 'South Beach/Willowbrook'
}

higher_ed = higher_ed.replace({"Name": higher_ed_rename})

x1 = higher_ed.loc[higher_ed['Name'] == 'Clinton/Chelsea']
x1.Name = 'Midtown'
x2 = higher_ed.loc[higher_ed['Name'] == 'Greenwich Village/Soho']
x2.Name = 'Financial District'
x3 = higher_ed.loc[higher_ed['Name'] == 'Morrisania/Crotona']
x3.Name = 'Belmont/East Tremont'
x4 = higher_ed.loc[higher_ed['Name'] == 'Mott Haven/Melrose']
x4.Name = 'Hunts Point/Longwood'

higher_ed = pd.concat([higher_ed, x1, x2, x3, x4]).reset_index(drop = True)

cd_name_dic = dict(zip(df["Name"], df["Community District"]))
higher_ed['Community District'] = higher_ed['Name'].map(cd_name_dic)

higher_ed = higher_ed[['Community District', 'Name', 'Indicator Category', 'Indicator', 'Indicator Description', 
                       '2000', '2006', '2010', '2017', '2018']]
higher_ed["2000"] = round(higher_ed["2000"]*100, 1)
higher_ed["2000"] = higher_ed["2000"].astype(str) + "%"
higher_ed["2006"] = round(higher_ed["2006"]*100, 1)
higher_ed["2006"] = higher_ed["2006"].astype(str) + "%"
higher_ed["2010"] = round(higher_ed["2010"]*100, 1)
higher_ed["2010"] = higher_ed["2010"].astype(str) + "%"
higher_ed["2017"] = round(higher_ed["2017"]*100, 1)
higher_ed["2017"] = higher_ed["2017"].astype(str) + "%"
higher_ed["2018"] = round(higher_ed["2018"]*100, 1)
higher_ed["2018"] = higher_ed["2018"].astype(str) + "%"

higher_ed["boro_cd"] = higher_ed["Community District"].map(stats_map_dic)


/anaconda3/lib/python3.6/site-packages/pandas/core/generic.py:5096: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  self[name] = value


In [122]:
# Adding the higher education info to the main dataframe
df = pd.concat([df, higher_ed]).reset_index(drop = True)

## Pushing data to MySQL 'community_demographics' table in 'nyc' database

In [132]:
# Create a connection engine to the MySQL database
host="192.168.4.38"
user="monty"
password=MYSQL_PASSWORD
db="nyc"
port=3306

conn = sqlalchemy.create_engine(f'mysql+mysqlconnector://{user}:{password}@{host}/{db}').connect()

df.to_sql(con=conn, name='community_demographics', if_exists='append', index=False)
                                
conn.close()

In [131]:
df

Community District                                  Name  \
0                  QN04                       Elmhurst/Corona   
1                  QN04                       Elmhurst/Corona   
2                  QN04                       Elmhurst/Corona   
3                  QN04                       Elmhurst/Corona   
4                  QN04                       Elmhurst/Corona   
5                  QN04                       Elmhurst/Corona   
6                  QN04                       Elmhurst/Corona   
7                  QN04                       Elmhurst/Corona   
8                  QN04                       Elmhurst/Corona   
9                  QN04                       Elmhurst/Corona   
10                 QN04                       Elmhurst/Corona   
11                 QN04                       Elmhurst/Corona   
12                 QN04                       Elmhurst/Corona   
13                 QN04                       Elmhurst/Corona   
14                 QN04                       Elmhurst/Corona   
15                 QN04                       Elmhurst/Corona   
16                 QN04                       Elmhurst/Corona   
17                 QN04                       Elmhurst/Corona   
18                 QN04                       Elmhurst/Corona   
19                 QN04                       Elmhurst/Corona   
20                 QN04                       Elmhurst/Corona   
21                 QN04                       Elmhurst/Corona   
22                 QN04                       Elmhurst/Corona   
23                 QN04                       Elmhurst/Corona   
24                 QN04                       Elmhurst/Corona   
25                 QN04                       Elmhurst/Corona   
26                 QN04                       Elmhurst/Corona   
27                 QN04                       Elmhurst/Corona   
28                 QN04                       Elmhurst/Corona   
29                 QN04                       Elmhurst/Corona   
30                 QN04                       Elmhurst/Corona   
31                 QN04                       Elmhurst/Corona   
32                 QN04                       Elmhurst/Corona   
33                 QN04                       Elmhurst/Corona   
34                 QN04                       Elmhurst/Corona   
35                 QN04                       Elmhurst/Corona   
36                 QN04                       Elmhurst/Corona   
37                 QN04                       Elmhurst/Corona   
38                 QN04                       Elmhurst/Corona   
39                 QN04                       Elmhurst/Corona   
40                 QN04                       Elmhurst/Corona   
41                 QN04                       Elmhurst/Corona   
42                 QN04                       Elmhurst/Corona   
43                 QN04                       Elmhurst/Corona   
44                 QN04                       Elmhurst/Corona   
45                 QN04                       Elmhurst/Corona   
46                 QN04                       Elmhurst/Corona   
47                 QN04                       Elmhurst/Corona   
48                 QN04                       Elmhurst/Corona   
49                 QN04                       Elmhurst/Corona   
50                 QN04                       Elmhurst/Corona   
51                 QN04                       Elmhurst/Corona   
52                 QN04                       Elmhurst/Corona   
53                 QN04                       Elmhurst/Corona   
54                 QN04                       Elmhurst/Corona   
55                 QN04                       Elmhurst/Corona   
56                 QN04                       Elmhurst/Corona   
57                 QN04                       Elmhurst/Corona   
58                 QN04                       Elmhurst/Corona   
59                 QN04                       Elmhurst/Corona   
60                 QN04                 

## Writing data to JSON file

In [163]:
j = (df.groupby(['boro_cd','Community District','Name'], as_index=False)
             .apply(lambda x: x[['Indicator Category','Indicator','Indicator Description','2018']].to_dict('r'))
             .reset_index()
             .rename(columns={0:'Variables'})
             .to_json(orient='records'))

In [140]:
# print(json.dumps(json.loads(j), indent=2, sort_keys=False))

final_json = json.dumps(json.loads(j), sort_keys=False)

output_path = '/Users/mareksalamon/Desktop/Policast/Code/App Demo/data/'
with open(output_path + 'cd_dem_data.txt', 'w') as outfile:
    json.dump(json.loads(j), outfile)